In [6]:
import requests
import json
import pandas as pd
from pathlib import Path
import sqlite3 as sql

In [87]:
api_data = requests.get("https://ghoapi.azureedge.net/api/WHOSIS_000004")
# Deserialization - the act of converting a string to an object
neonatal_mortality_rate = json.loads(api_data.text)
#neonatal_mortality_rate = mortality rate in births per 1000 live births.
text = neonatal_mortality_rate['value']


[{'Id': 19133175, 'IndicatorCode': 'WHOSIS_000004', 'SpatialDimType': 'REGION', 'SpatialDim': 'AFR', 'TimeDimType': 'YEAR', 'TimeDim': 2000, 'Dim1Type': 'SEX', 'Dim1': 'MLE', 'Dim2Type': None, 'Dim2': None, 'Dim3Type': None, 'Dim3': None, 'DataSourceDimType': None, 'DataSourceDim': None, 'Value': '424', 'NumericValue': 423.8763, 'Low': None, 'High': None, 'Comments': None, 'Date': '2018-05-07T09:06:17.653+02:00', 'TimeDimensionValue': '2000', 'TimeDimensionBegin': '2000-01-01T00:00:00+01:00', 'TimeDimensionEnd': '2000-12-31T00:00:00+01:00'}, {'Id': 19133176, 'IndicatorCode': 'WHOSIS_000004', 'SpatialDimType': 'REGION', 'SpatialDim': 'AFR', 'TimeDimType': 'YEAR', 'TimeDim': 2000, 'Dim1Type': 'SEX', 'Dim1': 'FMLE', 'Dim2Type': None, 'Dim2': None, 'Dim3Type': None, 'Dim3': None, 'DataSourceDimType': None, 'DataSourceDim': None, 'Value': '371', 'NumericValue': 371.4236, 'Low': None, 'High': None, 'Comments': None, 'Date': '2018-05-07T09:06:17.677+02:00', 'TimeDimensionValue': '2000', 'Time

In [81]:
dict_wanted_keys = {"Id","IndicatorCode","SpatialDim","TimeDim","Dim1","Value"}
l = [{k:v for k, v in i.items() if k in dict_wanted_keys} for i in text]
conn = sql.connect('database.db')
cur = conn.cursor()
# Check if table exists 
cur.execute(''' SELECT count(name) FROM sqlite_master WHERE type='table' AND name='Data' ''')
if cur.fetchone()[0]!=1 :
    cur.execute(''' CREATE TABLE IF NOT EXISTS Data (Id number,IndicatorCode text,SpatialDim text,TimeDim number,Dim1 text,Value number)''')
    for l_new in l:
        columns = ', '.join("`" + str(x).replace('/', '_') + "`" for x in l_new.keys())
        values = ', '.join("'" + str(x).replace('/', '_') + "'" for x in l_new.values())
        sqll = "INSERT INTO %s (%s) VALUES (%s);" % ('Data',columns,values)
        cur.execute(sqll)
    conn.commit()
conn.commit()
conn.close()


In [103]:
#csv file to json ==> sql
df = pd.read_csv(r"Country_income_rate.csv")
new_dict_region = df.to_dict()
keys_to_extract = ["Country_Code","IncomeGroup"]
dict_region_subset = {key: new_dict_region[key] for key in keys_to_extract}
conn = sql.connect('database.db')
cur = conn.cursor()
cur.execute(''' SELECT count(name) FROM sqlite_master WHERE type='table' AND name='country_income_data' ''')
if cur.fetchone()[0]!=1 :
    cur.execute(''' CREATE TABLE IF NOT EXISTS country_income_data (Country_Code text,IncomeGroup text)''')
    for i in range(2):
        subset_key = list(dict_region_subset.keys())[i]
        for l_new in subset_key:
            print(l_new)
            sqll = "INSERT INTO country_income_data (%s) VALUES %s;" % (columns,values)
            cur.execute(sqll)
conn.commit()
conn.close()

0


OperationalError: near ")": syntax error

In [96]:
keys_to_extract = ["Country_Code","IncomeGroup"]
dict_region_subset = {key: new_dict_region[key] for key in keys_to_extract}
dict_region_subset

{'Country_Code': {0: 'ABW',
  1: 'AFE',
  2: 'AFG',
  3: 'AFW',
  4: 'AGO',
  5: 'ALB',
  6: 'AND',
  7: 'ARB',
  8: 'ARE',
  9: 'ARG',
  10: 'ARM',
  11: 'ASM',
  12: 'ATG',
  13: 'AUS',
  14: 'AUT',
  15: 'AZE',
  16: 'BDI',
  17: 'BEL',
  18: 'BEN',
  19: 'BFA',
  20: 'BGD',
  21: 'BGR',
  22: 'BHR',
  23: 'BHS',
  24: 'BIH',
  25: 'BLR',
  26: 'BLZ',
  27: 'BMU',
  28: 'BOL',
  29: 'BRA',
  30: 'BRB',
  31: 'BRN',
  32: 'BTN',
  33: 'BWA',
  34: 'CAF',
  35: 'CAN',
  36: 'CEB',
  37: 'CHE',
  38: 'CHI',
  39: 'CHL',
  40: 'CHN',
  41: 'CIV',
  42: 'CMR',
  43: 'COD',
  44: 'COG',
  45: 'COL',
  46: 'COM',
  47: 'CPV',
  48: 'CRI',
  49: 'CSS',
  50: 'CUB',
  51: 'CUW',
  52: 'CYM',
  53: 'CYP',
  54: 'CZE',
  55: 'DEU',
  56: 'DJI',
  57: 'DMA',
  58: 'DNK',
  59: 'DOM',
  60: 'DZA',
  61: 'EAP',
  62: 'EAR',
  63: 'EAS',
  64: 'ECA',
  65: 'ECS',
  66: 'ECU',
  67: 'EGY',
  68: 'EMU',
  69: 'ERI',
  70: 'ESP',
  71: 'EST',
  72: 'ETH',
  73: 'EUU',
  74: 'FCS',
  75: 'FIN',
  76: 

In [112]:
 for i in range(2):
        subset_key = list(dict_region_subset.keys())[i]
        print(dict_region_subset[subset_key])
        for l_new in dict_region_subset[subset_key]:
            print(l_new)
            


{0: 'ABW', 1: 'AFE', 2: 'AFG', 3: 'AFW', 4: 'AGO', 5: 'ALB', 6: 'AND', 7: 'ARB', 8: 'ARE', 9: 'ARG', 10: 'ARM', 11: 'ASM', 12: 'ATG', 13: 'AUS', 14: 'AUT', 15: 'AZE', 16: 'BDI', 17: 'BEL', 18: 'BEN', 19: 'BFA', 20: 'BGD', 21: 'BGR', 22: 'BHR', 23: 'BHS', 24: 'BIH', 25: 'BLR', 26: 'BLZ', 27: 'BMU', 28: 'BOL', 29: 'BRA', 30: 'BRB', 31: 'BRN', 32: 'BTN', 33: 'BWA', 34: 'CAF', 35: 'CAN', 36: 'CEB', 37: 'CHE', 38: 'CHI', 39: 'CHL', 40: 'CHN', 41: 'CIV', 42: 'CMR', 43: 'COD', 44: 'COG', 45: 'COL', 46: 'COM', 47: 'CPV', 48: 'CRI', 49: 'CSS', 50: 'CUB', 51: 'CUW', 52: 'CYM', 53: 'CYP', 54: 'CZE', 55: 'DEU', 56: 'DJI', 57: 'DMA', 58: 'DNK', 59: 'DOM', 60: 'DZA', 61: 'EAP', 62: 'EAR', 63: 'EAS', 64: 'ECA', 65: 'ECS', 66: 'ECU', 67: 'EGY', 68: 'EMU', 69: 'ERI', 70: 'ESP', 71: 'EST', 72: 'ETH', 73: 'EUU', 74: 'FCS', 75: 'FIN', 76: 'FJI', 77: 'FRA', 78: 'FRO', 79: 'FSM', 80: 'GAB', 81: 'GBR', 82: 'GEO', 83: 'GHA', 84: 'GIB', 85: 'GIN', 86: 'GMB', 87: 'GNB', 88: 'GNQ', 89: 'GRC', 90: 'GRD', 91: 'GRL